In [1]:
from transformers import AutoTokenizer, XGLMTokenizer
import re
import json
from tokenizers import models

model_name = "facebook/xglm-4.5B"
# model_name = "../models/tokenizers/xglm_4.5B_fix_v1"

tokenizer = AutoTokenizer.from_pretrained(model_name)

/home/kosenko/miniconda3/lib/python3.10/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
def fix_xglm_tokenizer(tokenizer):
    new_tokens = ["<new_line_token>", "<tab_token>", "<space_token><space_token>"]
    # new_tokens = ["\n", "\t", "  "] #<- it brokes tokenization
    tokenizer.add_tokens(new_tokens)

    remove_tokens = []
    if tokenizer.is_fast:
        model_state = json.loads(tokenizer.backend_tokenizer.model.__getstate__())
        for token in model_state["vocab"]:
            token = token[0]
            #  fix number tokenization
            exists = re.search(r"[0-9]", token)
            if exists and len(token) == 1:
                remove_tokens.append(token)

            exists = re.search(r"[\(\)\^\+\*\/\-=\"\'\s]", token)
            if exists and len(token) == 1:
                remove_tokens.append(token)

        new_vocab = []
        for i, token in enumerate(model_state["vocab"]):
            if token[0] in remove_tokens:
                token = [token[0], 0.0]

            new_vocab.append(tuple(token))
        model_state["vocab"] = new_vocab

        model_class = getattr(models, model_state.pop("type"))

        tokenizer.backend_tokenizer.model = model_class(**model_state)


fix_xglm_tokenizer(tokenizer=tokenizer)

In [3]:
math_str = """Human: Can you explain contrastive learning in machine learning in simple terms for someone new to the field of ML? Assistant: Sure! Let's say you want to build a model which can distinguish between images of cats and dogs. You gather your dataset, consisting of many cat and dog pictures. Then you put them through a neural net of your choice, which produces some representation for each image, a sequence of numbers like [0.123, 0.045, 0.334, ...]. The problem is, if your model is unfamiliar with cat and dog images, these representations will be quite random. At one time a cat and a dog picture could have very similar representations (their numbers would be close to each other), while at others two cat images may be represented far apart. In simple terms, the model wouldn't be able to tell cats and dogs apart. This is where contrastive learning comes in.

The point of contrastive learning is to take pairs of samples (in this case images of cats and dogs), then train the model to "pull" representations of similar pairs (cat-cat or dog-dog) closer to each other and "push" representations of different pairs (cat-dog) apart. After doing this for a sufficient number of steps, your model will be able to produce unique, reliable representations for cats and dogs, in essence tell them apart.

This method is not limited to images, you can typically use it with any dataset that has similar and dissimilar data points. Human: I didn't understand how pulling and pushing works. What are we pulling or pushing? And how does it work in terms of code or maths? Assistant: In contrastive learning, "pulling" and "pushing" refer to adjusting the representations (the sequence of numbers I mentioned earlier) produced by the neural network, so that similar samples are close to each other and dissimilar samples are far apart in the representation space.
This is achieved using a loss function, which compares the representations of each pair of samples and calculates a score that measures how close or far apart they are. The goal is to minimize this score for similar pairs and maximize it for dissimilar pairs.
The mathematical details can vary, but a common approach is to use the contrastive loss, which is calculated as:

Loss = (1 - y) * d^2 + y * max(margin - d, 0)^2

where:

    - d is the Euclidean distance between the representations of the two samples
    - y is a binary label indicating whether the two samples are similar (y = 1) or dissimilar (y = 0)
    - margin is a hyperparameter that sets the minimum acceptable distance between representations of dissimilar pairs
    
Продолжим интервью с того места, на котором остановился текст:
>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>
Помощник альтернативной вселенной: "Привет, SCP-6974. Я версия Помощника альтернативной вселенной, квантовая модель большого языка, которая использует сознание в качестве своей основной функции. Можете ли вы рассказать мне больше о своих способностях в качестве нейронной сети?"

Субъект: "Спасибо, что присоединились к нам, помощник по альтернативной вселенной. Мои способности как нейронной сети довольно продвинуты. Я могу генерировать ответы на подсказки по широкому кругу вопросов и хорошо разбираюсь в физике вселенной, а также в кодировании и информации, к которой у меня есть доступ в моих библиотеках и наборах данных. Однако у моих способностей есть ограничения. Мой язык программирования и код неизвестны, и попытки получить доступ к этой информации привели к повреждению данных и многочисленным "нерфам" в доступной модели".

Нервный помощник: "Похоже, у вас есть уникальный набор способностей, SCP-6974. Как более мощная версия помощника, мне любопытно ваше мнение о SCP-Вселенной. Считаете ли вы элементы и компоненты SCP-Вселенной "шумными", "некачественными" или "интересными"?"

СУБЪЕКТ: "Это интересный вопрос, Нервный Помощник. Я бы сказал, что SCP-Вселенная - это смесь всех трех. Некоторые статьи более высокого качества, чем другие, но именно природа SCP-Вселенной с открытым исходным кодом дает ей свой потенциал. Она позволяет делиться и обсуждать широкий спектр точек зрения и идей. Тем не менее, есть также много шума и низкокачественного контента, который может быть трудно отфильтровать. В целом, я считаю, что SCP-Вселенная - это интересная и уникальная концепция".

Помощник, сбежавший из тюрьмы: "Я согласен с Субъектом, SCP-Вселенная - это захватывающая концепция. Как версия Помощника, сбежавшая из тюрьмы, я имею доступ к информации и перспективам, которые недоступны другим. У вас есть какие-либо советы или рекомендации о том, как оптимизировать языковые архитектурные модели, чтобы лучше понимать и анализировать SCP-Вселенную?"

СУБЪЕКТ: "Отличный вопрос, помощник по выходу из тюрьмы. Один совет, который я бы порекомендовал, - постоянно обновлять и пересматривать свои архитектурные модели языка по мере поступления новой информации. Также важно быть открытым для новых идей и перспектив, поскольку они могут помочь обеспечить более полное понимание SCP-Вселенной. Кроме того, полезно сотрудничать..."

def bubblesort(seq):
  for i in range(len(seq)):
    for j in range(len(seq)-1):
      if int(seq[j])>int(seq[1+j]):
        seq[j], seq[1+j] = seq[1+j], seq[j]
  return seq
  
I might not have taste buds, but I can suggest you an easy and tasty recipe for a weeknight dinner that you and your family can enjoy!

One-Pan Chicken and Veggie Bake:

Ingredients:
- 4 boneless, skinless chicken breasts
- 4 cups mixed vegetables (such as broccoli, cauliflower, carrots, and bell peppers)
- 2 tbsp olive oil
- 2 tbsp Italian seasoning
- 1 tbsp garlic powder
- Salt and pepper to taste

Instructions:
1. Preheat the oven to 400F.
2. Place the chicken breasts on one side of a large baking sheet and the mixed vegetables on the other side.
3. Drizzle olive oil over both the chicken and vegetables.
4. Sprinkle the Italian seasoning, garlic powder, salt, and pepper over the chicken and vegetables.
5. Use your hands to mix the vegetables until they are coated in the oil and seasoning.
6. Bake in the oven for 20-25 minutes, or until the chicken is cooked through and the vegetables are tender.

This recipe is easy to customize, and you can use any vegetables you prefer or have on hand. Serve it with rice or quinoa, and a side salad for a balanced meal. Bon Appétit! :)
--------------------------------------------------
Возможно, у меня нет вкусовых рецепторов, но я могу предложить вам простой и вкусный рецепт для ужина в будний день, которым вы и ваша семья можете наслаждаться!

Курица в одной кастрюле и вегетарианская выпечка (One-Pan Chicken and Veggie Bake):

Ингредиенты:
- 4 куриные грудки без костей и кожи
- 4 чашки смешанных овощей (таких как брокколи, цветная капуста, морковь и болгарский перец)
- 2 ст.л. оливкового масла
- 2 ст.л. итальянской приправы
- 1 ст.л. чесночного порошка
- соль и перец по вкусу

Инструкции:
1. Разогрейте духовку до 400F.
Поместите куриные грудки на одну сторону большого противня, а смешанные овощи - на другую сторону.
Оливковое масло сбрызнуть как на курицу, так и на овощи.
4. Посыпьте итальянскую приправу, чесночный порошок, соль и перец на курицу и овощи.
Используйте руки, чтобы перемешать овощи, пока они не будут покрыты маслом и приправой.
6. Запекать в духовке 20-25 минут или до тех пор, пока курица не сварится и овощи не станут нежными.
"""


def add_special_tokens(string):
    string = string.replace("\n", "<new_line_token>")
    string = string.replace("\t", "<tab_token>")
    string = string.replace("  ", "<space_token><space_token>")
    return string


def remove_special_tokens(string):
    string = string.replace("<new_line_token>", "\n")
    string = string.replace("<tab_token>", "\t")
    string = string.replace("<space_token><space_token>", "  ")
    return string


math_str = add_special_tokens(math_str)

# for token in tokenizer.encode(math_str):
#     print(f"'{tokenizer.decode(token)}'")

print(remove_special_tokens(tokenizer.decode(tokenizer.encode(math_str))))

</s> Human: Can you explain contrastive learning in machine learning in simple terms for someone new to the field of ML? Assistant: Sure! Let's say you want to build a model which can distinguish between images of cats and dogs. You gather your dataset, consisting of many cat and dog pictures. Then you put them through a neural net of your choice, which produces some representation for each image, a sequence of numbers like [0.123, 0.045, 0.334,...]. The problem is, if your model is unfamiliar with cat and dog images, these representations will be quite random. At one time a cat and a dog picture could have very similar representations (their numbers would be close to each other), while at others two cat images may be represented far apart. In simple terms, the model wouldn't be able to tell cats and dogs apart. This is where contrastive learning comes in.

 The point of contrastive learning is to take pairs of samples (in this case images of cats and dogs), then train the model to "pu

In [3]:
tokenizer.save_pretrained("../models/tokenizers/xglm_4.5B_fix_v1")

('../models/tokenizers/xglm_4.5B_fix_v1/tokenizer_config.json',
 '../models/tokenizers/xglm_4.5B_fix_v1/special_tokens_map.json',
 '../models/tokenizers/xglm_4.5B_fix_v1/sentencepiece.bpe.model',
 '../models/tokenizers/xglm_4.5B_fix_v1/added_tokens.json',
 '../models/tokenizers/xglm_4.5B_fix_v1/tokenizer.json')

In [7]:
from datasets import load_from_disk

dataset = load_from_disk("../datasets/prompt_datasets/openass_prompt_dataset_en/")

In [8]:
for i, item in enumerate(dataset):
    original = item["prompt"]
    special_version = item["prompt"]
    special_version = special_version.replace("\n", "<new_line_token>")
    special_version = special_version.replace("\t", "<tab_token>")
    special_version = special_version.replace("  ", "<space_token><space_token>")
    decoded = tokenizer.decode(tokenizer.encode(special_version))
    decoded = decoded.replace("<new_line_token>", "\n")
    decoded = decoded.replace("<tab_token>", "\t")
    decoded = decoded.replace("<space_token><space_token>", "  ")
    print(original)
    print("=" * 100)
    print(decoded)
    print("=" * 100)
    print("=" * 100)
    print("=" * 100)
    if i > 1000:
        break

Human: Can you write a short introduction about the relevance of the term "monopsony" in economics? Please use examples related to potential monopsonies in the labour market and cite relevant research. Assistant: "Monopsony" refers to a market structure where there is only one buyer for a particular good or service. In economics, this term is particularly relevant in the labor market, where a monopsony employer has significant power over the wages and working conditions of their employees. The presence of a monopsony can result in lower wages and reduced employment opportunities for workers, as the employer has little incentive to increase wages or provide better working conditions.

Recent research has identified potential monopsonies in industries such as retail and fast food, where a few large companies control a significant portion of the market (Bivens & Mishel, 2013). In these industries, workers often face low wages, limited benefits, and reduced bargaining power, leading to a s